In [1140]:
import gurobipy as grb
from gurobipy import GRB
import scipy.sparse as spr
import numpy as np
import random
import matplotlib.pyplot as plt
#from sympy import symbols, Rational
from IPython.display import display, Math, Markdown
import numpy.ma as ma


In [1141]:
%run /Users/enzo-macmini/auction_alg_ITU/parallel_auction_ITU.ipynb

In [1142]:
n_small = 5
m_small = 3
example_small = OneToOneITU( n = n_small,m = m_small, size_params= (2,24) , random_seed= 778, lbs =(0,0), tol = 1e-1)

In [1143]:
example_small.A_ij

array([[1., 1., 1.],
       [1., 1., 1.],
       [1., 1., 1.],
       [1., 1., 1.],
       [1., 1., 1.]])

In [1916]:
def iteration(self,i_ent, mu, V_j):
    C  = np.zeros(self.n, dtype= bool)
    C_i_ent = np.zeros(self.n, dtype= bool)
    C[i_ent] = 1
    B = np.ones(self.m, dtype= bool)
    L_j = np.ones(self.m, dtype= int) *(self.n + 1)
    d_j = np.ones(self.m, dtype= bool) * np.inf

    iter = 0
    while np.any(C == 1):
        iter += 1
        i = np.argmax(C)
        print(f"iter {iter}, i: {i}")
        C[i] = 0
        C_i_ent[i] = 1
        U_ij_s = self.get_U_ij(V_j, i)[0]

        π_i = np.max(U_ij_s)
        
        suboptimal_js = U_ij_s < π_i
        #print(suboptimal_js)
        d_j[suboptimal_js] = np.minimum(d_j[suboptimal_js], π_i - np.maximum(U_ij_s[suboptimal_js], self.lb_U )) 
        #print(np.shape(U_ij_s))
        unissigne_optimal_j = np.where((mu.sum(0) == 0) * (π_i == U_ij_s))[0]

        if len(unissigne_optimal_j)> 0 :
            # L_j[unissigne_optimal_j[0]] = i
            # mu[:, L_j < self.n +1 ] = 0
            # mu[L_j [L_j < self.n +1], L_j < self.n +1 ] = 1
            # #print(  np.shape(self.get_U_ij(V_j, L_j [L_j < self.n +1] )))
            # #print( np.shape( np.ones(((L_j < self.n +1).sum() ,1 ))))
            # # print(  np.concatenate( [self.get_U_ij(V_j, L_j [L_j < self.n +1] ), 
            # #                                 np.ones(((L_j < self.n +1).sum() ,1 ))], axis= 1)     ) 
            # w_i_s = np.sort( np.concatenate([self.get_U_ij(V_j, L_j [L_j < self.n +1] ), 
            #                                 np.ones(((L_j < self.n +1).sum() ,1 ))] , axis = 1))[:,-2]
            # print(w_i_s)
            # V_j[L_j < self.n +1] = self.get_V_ij(L_j [L_j < self.n +1]  , L_j < self.n +1 ,  w_i_s)

            


            i_t = i
            j_t = unissigne_optimal_j[0]
            iter_loop = 0
            while i_t != i_ent :
                #print(i_t)
                j_t_plus_1 = np.where(mu[i_t,: ]>0)[0][0]
                #print(j_t_plus_1)
                mu[i_t,: ] = 0
                mu[i_t, j_t] = 1
                #print(np.shape(self.get_U_ij(V_j, i_t)[0]))
                w_i_s = np.sort( np.concatenate([self.get_U_ij(V_j, i_t)[0], [self.lb_U]]))[-2]
                #print(np.shape(w_i_s))
                #print(w_i_s)
                V_j[j_t] = self.get_V_ij(i_t  , j_t,  w_i_s)




                j_t = j_t_plus_1
                i_t = L_j[j_t]
                iter_loop += 1 

                

            
            mu[i_t,: ] = 0
            mu[i_t, j_t] = 1


            #V_j[j] = self.get_V_ij(i,j,w_i)[0]
            # print(f"j : {j}")
            print(L_j)
            print("augmentation")
            return mu, V_j


        for j in np.where(B * (~suboptimal_js) >0)[0]:
            
            #U_ij = self.get_U_ij(V_j, i, j)[0]
            if mu[:,j].sum() == 1:
                i_j = np.argmax(mu[:,j])
                B[j] = 0
                C[i_j] = 1
                
                L_j[j] = i if L_j[j] == self.n + 1 else None
                #print(f"j : {j}")
                #print(L_j)
                print(f"{i} -> {j} ")
                #break
            # if mu[:,j].sum() == 0:
            #     # perform augmentation
                
            #     L_j[j] = i
            #     mu[:, L_j < self.n +1 ] = 0
            #     mu[L_j [L_j < self.n +1], L_j < self.n +1 ] = 1
            #     w_i_s = np.sort(self.get_U_ij(V_j, L_j [L_j < self.n +1] ), axis = 1)[:,-2]
            #     V_j[L_j < self.n +1] = self.get_V_ij(L_j [L_j < self.n +1]  , L_j < self.n +1 ,  w_i_s)
            #     #V_j[j] = self.get_V_ij(i,j,w_i)[0]
            #     print(f"AaaAAAAAA")

            #     return mu, V_j


           

    
    return C_i_ent, B * (d_j < np.inf), d_j

OneToOneITU.iteration = iteration

In [1917]:
np.ones((1,1))

array([[1.]])

In [1964]:
mu_ex = np.zeros([n_small,m_small])
V_ex = np.ones(example_small.m) * example_small.lb_V
perm_unassigned = np.zeros(example_small.n, dtype= bool)

In [1965]:
example_small.B_ij

array([[9, 3, 7, 8, 6, 0, 9, 5],
       [2, 9, 6, 6, 0, 4, 8, 5],
       [1, 2, 8, 5, 3, 3, 6, 3],
       [4, 0, 9, 5, 8, 6, 9, 4],
       [3, 5, 2, 5, 6, 9, 3, 0],
       [1, 4, 5, 9, 5, 5, 6, 6],
       [4, 9, 5, 4, 7, 8, 4, 0],
       [2, 4, 8, 5, 7, 3, 9, 7]])

In [1971]:
i_ent = np.where((mu_ex.sum(1) == 0) * (~perm_unassigned) > 0)[0][0]
iter_values = example_small.iteration(i_ent, mu_ex, V_ex )

if len(iter_values) == 2:
    mu_ex, V_ex = iter_values

else:
    C_i, B, d = iter_values
    print(V_ex[6])
    V_ex[~B] += np.min(d)
    print(V_ex[6])
    print(B)
    print(d)
    print(d.min())
    

perm_unassigned = np.all(example_small.get_U_ij(V_ex , np.arange(example_small.n)) <= example_small.lb_U, axis = 1)
mu_ex[perm_unassigned,:] = 0

iter 1, i: 1
1 -> 6 
iter 2, i: 0
4.0
5.571428571428571
[ True  True  True  True  True  True False  True]
[2.         1.57142857 2.         2.         2.         2.
        inf 2.        ]
1.5714285714285712


In [1967]:
V_ex

array([4., 4., 4., 4., 4., 4., 4., 4.])

In [1968]:
perm_unassigned

array([False, False,  True, False, False, False, False, False])

In [1969]:
mu_ex

array([[0., 0., 0., 0., 0., 0., 1., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0.]])

In [1970]:
example_small.get_U_ij(V_ex , np.arange(6)).round(3)

array([[ -1.667,   2.429, -11.   ,   1.6  ,  -1.   , -16.   ,   4.   ,
         -0.333],
       [ -2.   , -15.   ,  -6.   ,  -1.   ,  -0.889,   2.   ,   7.2  ,
          4.111],
       [ -1.667,  -2.   ,  -8.   ,  -5.667,  -1.571,   1.222,  -4.   ,
         -1.571],
       [ -2.   ,  -2.222,  -7.   ,   1.667,   6.   ,   2.   ,   7.5  ,
          1.   ],
       [ -1.   ,  -7.   , -10.   ,  -3.   ,   1.5  ,   3.667,  -2.333,
         -2.   ],
       [ -3.   , -12.   , -23.   ,  -1.667,   1.667,   1.   ,   2.   ,
          5.2  ]])

In [1733]:
def ITU_auction(self):
    mu_ij = np.zeros([self.n,self.m])
    V_j = np.ones(self.m) * self.lb_V
    perm_unassigned = np.zeros(self.n, dtype= bool)
    
    while True:
        i_ent = np.where((mu_ij.sum(1) == 0) * (~perm_unassigned) > 0)[0]
        if len(i_ent) == 0:
            break
        else:
            i_ent = i_ent[0]
        iter_values = self.iteration(i_ent, mu_ij, V_j )

        if len(iter_values) == 2:
            mu_ij, V_j = iter_values

        else:
            C_i, B, d = iter_values
            V_j[~B] += np.min(d)
            print(B)
            print(d)
            

        perm_unassigned = np.all(self.get_U_ij(V_j , np.arange(self.n)) <= self.lb_U, axis = 1)
        mu_ij[perm_unassigned,:] = 0

        


    id_i , id_j  =  np.where(mu_ij == 1)
    
    U_i = np.ones(self.n) * self.lb_U
    U_i[id_i] = self.get_U_ij(V_j, id_i)[np.arange(len(id_i)), id_j]   

    return mu_ij,U_i, V_j, perm_unassigned * 1

OneToOneITU.ITU_auction = ITU_auction

In [1690]:
n_small = 8
m_small = 8
example_small = OneToOneITU( n = n_small,m = m_small, size_params= (10,10) , random_seed= 4409, lbs =(2,4), tol = 0)

In [1689]:
mu_ex , U_ex,  V_ex , perm_ = example_small.ITU_auction()

iter 1, i: 0
[9 9 9 9 9 9 9 9]
augmentation
iter 1, i: 1
j : 6
[9 9 9 9 9 9 1 9]
1 <- 6 
iter 2, i: 0
[ True  True  True  True  True  True False  True]
[2.         1.57142857 2.         2.         2.         2.
        inf 2.        ]
iter 1, i: 1
j : 6
[9 9 9 9 9 9 1 9]
1 <- 6 
iter 2, i: 0
0
6
[9 9 9 9 9 9 1 9]
augmentation
iter 1, i: 3
j : 6
[9 9 9 9 9 9 3 9]
3 <- 6 
iter 2, i: 1
[ True  True  True  True  True  True False  True]
[4.88571429 4.88571429 4.88571429 4.88571429 0.91071429 4.88571429
        inf 2.77460317]
iter 1, i: 3
j : 6
[9 9 9 9 9 9 3 9]
3 <- 6 
iter 2, i: 1
[ True  True  True  True  True  True False  True]
[4.56919643 4.56919643 4.56919643 4.56919643 0.56919643 4.56919643
        inf 2.59246032]
iter 1, i: 3
j : 6
[9 9 9 9 9 9 3 9]
3 <- 6 
iter 2, i: 1
[ True  True  True  True  True  True False  True]
[4.35574777 4.35574777 4.35574777 4.35574777 0.35574777 4.35574777
        inf 2.47862103]
iter 1, i: 3
j : 6
[9 9 9 9 9 9 3 9]
3 <- 6 
iter 2, i: 1
[ True  True  Tru

KeyboardInterrupt: 

In [1677]:
example_small.check_all((mu_ex , U_ex , V_ex ))

____
<h1>Feasibility</h1>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

#matched: 10 over 10

____
<h1>Generalized Complementary Slackness</h1>

...

____
<h1>Individual Rationality</h1>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

<IPython.core.display.Math object>

In [1626]:
example_small.get_U_ij(V_ex , np.arange(10))

IndexError: index 5 is out of bounds for axis 0 with size 5